## Read the File

In [1]:
# dbase.py file

import pyodbc
import pandas as pd

def readFile():
    #needs own button
    try:

        conn = pyodbc.connect('Driver={SQL Server};Server=40.69.217.124,1455;Database=LaborexDB;Trusted_Connection=no;UID=Lab;PWD=Lab@2019;')
        cursor = conn.cursor()

        df = pd.read_sql_query(
        '''select * FROM LaborexDB.dbo.View_DataToForecast''', conn, parse_dates=['Date'], index_col='Date')

        df = df.rename(columns={'ProductName':'PRODUCT', 'OrderedQTY':'Sale'})
        df.index.names=['Month']
        df = df.dropna()

    except:

        df = pd.read_excel('data.xlsx')
        df = df.rename(columns={'Product Type':'Category'})
        df.index.names=['Month']

    return df


## Process and Prepare data

In [14]:
# processing.py file

from dbase import readFile
import pandas as pd
import numpy as np
import itertools
import time
from sklearn.preprocessing import RobustScaler
import datetime as dt


def DataProcessing():

    data = readFile()

    data = data.dropna()

    product_dictionary = {}

    products = list(data.PRODUCT.unique())

    for product in products:
        product_dictionary["df_{}".format(product)] = data[data['PRODUCT']==product]
        
    #debugging
    #print(product_dictionary)

    return product_dictionary


def DataPreparation():
    #might want to use self keyword to access dictionary
    data = DataProcessing()

    feature_columns = ['AV3MT01', 'AV6MT01']

    feature_transformer = RobustScaler()
    sales_transformer = RobustScaler()

    for item in data:
        data["{}".format(item)]['Month'] = data["{}".format(item)].Month.dt.month
        #
        #For Data Split
        #
        train_size = int(len(data["{}".format(item)].drop(columns=['PRODUCT'], axis=1)) * 0.75)
        test_size = len(data["{}".format(item)]) - train_size
        train, test = data["{}".format(item)].iloc[0:train_size], data["{}".format(item)].iloc[train_size:len(data["{}".format(item)])]
        train, test = train.drop(columns='PRODUCT'), test.drop(columns='PRODUCT')

        # 
        # For Data transformation and scaling
        # 
        try:
            
            feature_transformer = feature_transformer.fit(train[feature_columns].to_numpy())
            sales_transformer = sales_transformer.fit(train[['Sale']])
            
            train.loc[:, feature_columns] = feature_transformer.transform(train[feature_columns].to_numpy())
            train['Sale'] = sales_transformer.transform(train[['Sale']])

            test.loc[:, feature_columns] = feature_transformer.transform(test[feature_columns].to_numpy())
            test['Sale'] = sales_transformer.transform(test[['Sale']])
        except:
            print('ValueError: Found array with 0 sample(s)')

        TIME_STEPS = 3
        
        if train.shape[0] < 20 and test.shape[0] < 9:
            pass
        elif train.shape[0] >= 20 and test.shape[0] >= 9:
            X_train, y_train = create_data(train, train.Sale, time_steps=TIME_STEPS)
            X_test, y_test = create_data(test, test.Sale, time_steps=TIME_STEPS)
            
            print(f'Xtrain {X_train}')
            print(f'Xtest{X_test}')

    return #some list or dictionary

        

        
def create_data(X, y, time_steps=1):
    Xs, ys = [], []
    for i in range(len(X) - time_steps):
        v = X.iloc[i: (i + time_steps)].to_numpy()
        Xs.append(v)
        ys.append(y.iloc[i + time_steps])

    return np.array(Xs), np.array(ys)

In [9]:
DataProcessing()

{'df_BIPRETERAX 5MG/1.25MG TABS 30':        Unnamed: 0                        PRODUCT  NOART   QTY  ENROUTE  MODE  \
Month                                                                          
0              43  BIPRETERAX 5MG/1.25MG TABS 30  86380   777     3500     2   
1              44  BIPRETERAX 5MG/1.25MG TABS 30  86380   777     3500     2   
2              45  BIPRETERAX 5MG/1.25MG TABS 30  86380   310     3500     2   
3              46  BIPRETERAX 5MG/1.25MG TABS 30  86380   310     3500     2   
4              47  BIPRETERAX 5MG/1.25MG TABS 30  86380     0     3450     7   
5              48  BIPRETERAX 5MG/1.25MG TABS 30  86380  2695      350     7   
6              49  BIPRETERAX 5MG/1.25MG TABS 30  86380  2754      480     7   
7              50  BIPRETERAX 5MG/1.25MG TABS 30  86380  2245      500     7   
8              51  BIPRETERAX 5MG/1.25MG TABS 30  86380  1630      500     7   
9              52  BIPRETERAX 5MG/1.25MG TABS 30  86380  1630      500     7   
10 

{'df_BIPRETERAX 5MG/1.25MG TABS 30':        Unnamed: 0                        PRODUCT  NOART   QTY  ENROUTE  MODE  \
 Month                                                                          
 0              43  BIPRETERAX 5MG/1.25MG TABS 30  86380   777     3500     2   
 1              44  BIPRETERAX 5MG/1.25MG TABS 30  86380   777     3500     2   
 2              45  BIPRETERAX 5MG/1.25MG TABS 30  86380   310     3500     2   
 3              46  BIPRETERAX 5MG/1.25MG TABS 30  86380   310     3500     2   
 4              47  BIPRETERAX 5MG/1.25MG TABS 30  86380     0     3450     7   
 5              48  BIPRETERAX 5MG/1.25MG TABS 30  86380  2695      350     7   
 6              49  BIPRETERAX 5MG/1.25MG TABS 30  86380  2754      480     7   
 7              50  BIPRETERAX 5MG/1.25MG TABS 30  86380  2245      500     7   
 8              51  BIPRETERAX 5MG/1.25MG TABS 30  86380  1630      500     7   
 9              52  BIPRETERAX 5MG/1.25MG TABS 30  86380  1630      500  

In [15]:
DataPreparation()

Xtrain [[[43 86380 777 ... 43 'Anti-hypertensive' 'Available']
  [44 86380 777 ... 43 'Anti-hypertensive' 'Available']
  [45 86380 310 ... 43 'Anti-hypertensive' 'Available']]

 [[44 86380 777 ... 43 'Anti-hypertensive' 'Available']
  [45 86380 310 ... 43 'Anti-hypertensive' 'Available']
  [46 86380 310 ... 43 'Anti-hypertensive' 'Available']]

 [[45 86380 310 ... 43 'Anti-hypertensive' 'Available']
  [46 86380 310 ... 43 'Anti-hypertensive' 'Available']
  [47 86380 0 ... 43 'Anti-hypertensive' 'Available']]

 ...

 [[69 86380 1807 ... 43 'Anti-hypertensive' 'Available']
  [70 86380 2687 ... 43 'Anti-hypertensive' 'Available']
  [71 86380 2465 ... 43 'Anti-hypertensive' 'Available']]

 [[70 86380 2687 ... 43 'Anti-hypertensive' 'Available']
  [71 86380 2465 ... 43 'Anti-hypertensive' 'Available']
  [72 86380 2490 ... 43 'Anti-hypertensive' 'Available']]

 [[71 86380 2465 ... 43 'Anti-hypertensive' 'Available']
  [72 86380 2490 ... 43 'Anti-hypertensive' 'Available']
  [73 86380 2179 ..

Xtrain [[[558 113655 540 ... 51 'Anti-TB' 'Available']
  [559 113655 531 ... 51 'Anti-TB' 'Available']
  [560 113655 54 ... 51 'Anti-TB' 'Available']]

 [[559 113655 531 ... 51 'Anti-TB' 'Available']
  [560 113655 54 ... 51 'Anti-TB' 'Available']
  [561 113655 0 ... 51 'Anti-TB' 'Available']]

 [[560 113655 54 ... 51 'Anti-TB' 'Available']
  [561 113655 0 ... 51 'Anti-TB' 'Available']
  [562 113655 0 ... 51 'Anti-TB' 'Available']]

 ...

 [[590 113655 8 ... 51 'Anti-TB' 'Available']
  [591 113655 3032 ... 51 'Anti-TB' 'Available']
  [592 113655 3032 ... 51 'Anti-TB' 'Available']]

 [[591 113655 3032 ... 51 'Anti-TB' 'Available']
  [592 113655 3032 ... 51 'Anti-TB' 'Available']
  [593 113655 1845 ... 51 'Anti-TB' 'Available']]

 [[592 113655 3032 ... 51 'Anti-TB' 'Available']
  [593 113655 1845 ... 51 'Anti-TB' 'Available']
  [594 113655 1845 ... 51 'Anti-TB' 'Available']]]
Xtest[[[596 113655 1845 0 2 0.9680111265646731 0.2186827378390013 0 12
   1.9521531100478469 Timestamp('2018-03-27

Xtrain [[[1131 101960 0 ... 37 'Cough Syrup' 'Available']
  [1132 101960 0 ... 37 'Cough Syrup' 'Available']
  [1133 101960 0 ... 37 'Cough Syrup' 'Available']]

 [[1132 101960 0 ... 37 'Cough Syrup' 'Available']
  [1133 101960 0 ... 37 'Cough Syrup' 'Available']
  [1134 101960 0 ... 37 'Cough Syrup' 'Available']]

 [[1133 101960 0 ... 37 'Cough Syrup' 'Available']
  [1134 101960 0 ... 37 'Cough Syrup' 'Available']
  [1135 101960 3 ... 37 'Cough Syrup' 'Available']]

 ...

 [[1152 101960 576 ... 37 'Cough Syrup' 'Available']
  [1153 101960 529 ... 37 'Cough Syrup' 'Available']
  [1154 101960 1887 ... 37 'Cough Syrup' 'Available']]

 [[1153 101960 529 ... 37 'Cough Syrup' 'Available']
  [1154 101960 1887 ... 37 'Cough Syrup' 'Available']
  [1155 101960 1478 ... 37 'Cough Syrup' 'Available']]

 [[1154 101960 1887 ... 37 'Cough Syrup' 'Available']
  [1155 101960 1478 ... 37 'Cough Syrup' 'Available']
  [1156 101960 753 ... 37 'Cough Syrup' 'Available']]]
Xtest[[[1158 101960 415 0 3 -0.262

Xtrain [[[1564 58184 517 ... 37 'Anthelmintics' 'Available']
  [1565 58184 734 ... 37 'Anthelmintics' 'Available']
  [1566 58184 1804 ... 37 'Anthelmintics' 'Available']]

 [[1565 58184 734 ... 37 'Anthelmintics' 'Available']
  [1566 58184 1804 ... 37 'Anthelmintics' 'Available']
  [1567 58184 1804 ... 37 'Anthelmintics' 'Available']]

 [[1566 58184 1804 ... 37 'Anthelmintics' 'Available']
  [1567 58184 1804 ... 37 'Anthelmintics' 'Available']
  [1568 58184 685 ... 37 'Anthelmintics' 'Available']]

 ...

 [[1585 58184 1360 ... 37 'Anthelmintics' 'Available']
  [1586 58184 961 ... 37 'Anthelmintics' 'Available']
  [1587 58184 531 ... 37 'Anthelmintics' 'Available']]

 [[1586 58184 961 ... 37 'Anthelmintics' 'Available']
  [1587 58184 531 ... 37 'Anthelmintics' 'Available']
  [1588 58184 366 ... 37 'Anthelmintics' 'Available']]

 [[1587 58184 531 ... 37 'Anthelmintics' 'Available']
  [1588 58184 366 ... 37 'Anthelmintics' 'Available']
  [1589 58184 141 ... 37 'Anthelmintics' 'Available']

Xtrain [[[1834 71073 116 ... 37 'Anti-hypertensive' 'Available']
  [1835 71073 51 ... 37 'Anti-hypertensive' 'Available']
  [1836 71073 46 ... 37 'Anti-hypertensive' 'Available']]

 [[1835 71073 51 ... 37 'Anti-hypertensive' 'Available']
  [1836 71073 46 ... 37 'Anti-hypertensive' 'Available']
  [1837 71073 46 ... 37 'Anti-hypertensive' 'Available']]

 [[1836 71073 46 ... 37 'Anti-hypertensive' 'Available']
  [1837 71073 46 ... 37 'Anti-hypertensive' 'Available']
  [1838 71073 620 ... 37 'Anti-hypertensive' 'Available']]

 ...

 [[1855 71073 614 ... 37 'Anti-hypertensive' 'Available']
  [1856 71073 497 ... 37 'Anti-hypertensive' 'Available']
  [1857 71073 444 ... 37 'Anti-hypertensive' 'Available']]

 [[1856 71073 497 ... 37 'Anti-hypertensive' 'Available']
  [1857 71073 444 ... 37 'Anti-hypertensive' 'Available']
  [1858 71073 452 ... 37 'Anti-hypertensive' 'Available']]

 [[1857 71073 444 ... 37 'Anti-hypertensive' 'Available']
  [1858 71073 452 ... 37 'Anti-hypertensive' 'Available'

...

Xtrain [[[12958 105382 891 ... 45 'Vaccine' 'Available']
  [12959 105382 816 ... 45 'Vaccine' 'Available']
  [12960 105382 1505 ... 45 'Vaccine' 'Available']]

 [[12959 105382 816 ... 45 'Vaccine' 'Available']
  [12960 105382 1505 ... 45 'Vaccine' 'Available']
  [12961 105382 1505 ... 45 'Vaccine' 'Available']]

 [[12960 105382 1505 ... 45 'Vaccine' 'Available']
  [12961 105382 1505 ... 45 'Vaccine' 'Available']
  [12962 105382 1594 ... 45 'Vaccine' 'Available']]

 ...

 [[12985 105382 2858 ... 45 'Vaccine' 'Available']
  [12986 105382 3959 ... 45 'Vaccine' 'Available']
  [12987 105382 1843 ... 45 'Vaccine' 'Available']]

 [[12986 105382 3959 ... 45 'Vaccine' 'Available']
  [12987 105382 1843 ... 45 'Vaccine' 'Available']
  [12988 105382 729 ... 45 'Vaccine' 'Available']]

 [[12987 105382 1843 ... 45 'Vaccine' 'Available']
  [12988 105382 729 ... 45 'Vaccine' 'Available']
  [12989 105382 0 ... 45 'Vaccine' 'Available']]]
Xtest[[[12991 105382 5591 2000 3 -1.754208754208754 -0.5941422594

Xtrain [[[13242 10191 1795 ... 35 'Vaccine' 'Available']
  [13243 10191 1671 ... 35 'Vaccine' 'Available']
  [13244 10191 183 ... 35 'Vaccine' 'Available']]

 [[13243 10191 1671 ... 35 'Vaccine' 'Available']
  [13244 10191 183 ... 35 'Vaccine' 'Available']
  [13245 10191 183 ... 35 'Vaccine' 'Available']]

 [[13244 10191 183 ... 35 'Vaccine' 'Available']
  [13245 10191 183 ... 35 'Vaccine' 'Available']
  [13246 10191 183 ... 35 'Vaccine' 'Available']]

 ...

 [[13262 10191 0 ... 35 'Vaccine' 'Available']
  [13263 10191 0 ... 35 'Vaccine' 'Available']
  [13264 10191 0 ... 35 'Vaccine' 'Available']]

 [[13263 10191 0 ... 35 'Vaccine' 'Available']
  [13264 10191 0 ... 35 'Vaccine' 'Available']
  [13265 10191 0 ... 35 'Vaccine' 'Available']]

 [[13264 10191 0 ... 35 'Vaccine' 'Available']
  [13265 10191 0 ... 35 'Vaccine' 'Available']
  [13266 10191 0 ... 35 'Vaccine' 'Available']]]
Xtest[[[13268 10191 3572 0 7 -0.9229852169766333 -1.4249662009914377 1 10
   -0.5803806734992679 Timestamp('

Xtrain [[[13505 83133 0 ... 48 'Local Analgesic' 'Available']
  [13506 83133 0 ... 48 'Local Analgesic' 'Available']
  [13507 83133 0 ... 48 'Local Analgesic' 'Available']]

 [[13506 83133 0 ... 48 'Local Analgesic' 'Available']
  [13507 83133 0 ... 48 'Local Analgesic' 'Available']
  [13508 83133 0 ... 48 'Local Analgesic' 'Available']]

 [[13507 83133 0 ... 48 'Local Analgesic' 'Available']
  [13508 83133 0 ... 48 'Local Analgesic' 'Available']
  [13509 83133 0 ... 48 'Local Analgesic' 'Available']]

 ...

 [[13535 83133 134 ... 48 'Local Analgesic' 'Available']
  [13536 83133 32 ... 48 'Local Analgesic' 'Available']
  [13537 83133 32 ... 48 'Local Analgesic' 'Available']]

 [[13536 83133 32 ... 48 'Local Analgesic' 'Available']
  [13537 83133 32 ... 48 'Local Analgesic' 'Available']
  [13538 83133 32 ... 48 'Local Analgesic' 'Available']]

 [[13537 83133 32 ... 48 'Local Analgesic' 'Available']
  [13538 83133 32 ... 48 'Local Analgesic' 'Available']
  [13539 83133 32 ... 48 'Local A

Xtrain [[[13897 72468 9738 ... 37 'Anthelmintics' 'Available']
  [13898 72468 4912 ... 37 'Anthelmintics' 'Available']
  [13899 72468 13206 ... 37 'Anthelmintics' 'Available']]

 [[13898 72468 4912 ... 37 'Anthelmintics' 'Available']
  [13899 72468 13206 ... 37 'Anthelmintics' 'Available']
  [13900 72468 13206 ... 37 'Anthelmintics' 'Available']]

 [[13899 72468 13206 ... 37 'Anthelmintics' 'Available']
  [13900 72468 13206 ... 37 'Anthelmintics' 'Available']
  [13901 72468 4592 ... 37 'Anthelmintics' 'Available']]

 ...

 [[13918 72468 10342 ... 37 'Anthelmintics' 'Available']
  [13919 72468 8511 ... 37 'Anthelmintics' 'Available']
  [13920 72468 7141 ... 37 'Anthelmintics' 'Available']]

 [[13919 72468 8511 ... 37 'Anthelmintics' 'Available']
  [13920 72468 7141 ... 37 'Anthelmintics' 'Available']
  [13921 72468 5385 ... 37 'Anthelmintics' 'Available']]

 [[13920 72468 7141 ... 37 'Anthelmintics' 'Available']
  [13921 72468 5385 ... 37 'Anthelmintics' 'Available']
  [13922 72468 3581

Xtrain [[[14156 102544 2194 ... 37 'Antibiotic' 'Available']
  [14157 102544 1635 ... 37 'Antibiotic' 'Available']
  [14158 102544 3428 ... 37 'Antibiotic' 'Available']]

 [[14157 102544 1635 ... 37 'Antibiotic' 'Available']
  [14158 102544 3428 ... 37 'Antibiotic' 'Available']
  [14159 102544 3428 ... 37 'Antibiotic' 'Available']]

 [[14158 102544 3428 ... 37 'Antibiotic' 'Available']
  [14159 102544 3428 ... 37 'Antibiotic' 'Available']
  [14160 102544 2844 ... 37 'Antibiotic' 'Available']]

 ...

 [[14177 102544 1721 ... 37 'Antibiotic' 'Available']
  [14178 102544 913 ... 37 'Antibiotic' 'Available']
  [14179 102544 1252 ... 37 'Antibiotic' 'Available']]

 [[14178 102544 913 ... 37 'Antibiotic' 'Available']
  [14179 102544 1252 ... 37 'Antibiotic' 'Available']
  [14180 102544 1024 ... 37 'Antibiotic' 'Available']]

 [[14179 102544 1252 ... 37 'Antibiotic' 'Available']
  [14180 102544 1024 ... 37 'Antibiotic' 'Available']
  [14181 102544 355 ... 37 'Antibiotic' 'Available']]]
Xtest[